In [2]:
import xarray as xr
import ocf_blosc2
import pandas as pd
import numpy as np
import warnings
warnings.filterwarnings("ignore")
import numpy as np
from pytorch_forecasting.models import TemporalFusionTransformer
from pytorch_forecasting import Baseline, TemporalFusionTransformer, TimeSeriesDataSet
from pytorch_forecasting.metrics import QuantileLoss
import torch
import warnings
warnings.filterwarnings("ignore")

In [3]:
test_data = pd.read_csv("../result_data/tft_data_36_test.csv")

In [4]:
test_data

Unnamed: 0    ss_id            init_time             step  \
0          48348  26985.0  2018-11-15 12:00:00  0 days 00:00:00   
1          48349  26985.0  2018-11-15 12:00:00  0 days 01:00:00   
2          48350  26985.0  2018-11-15 12:00:00  0 days 02:00:00   
3          48351  26985.0  2018-11-15 12:00:00  0 days 03:00:00   
4          48352  26985.0  2018-11-15 12:00:00  0 days 04:00:00   
...          ...      ...                  ...              ...   
3595       51943  27064.0  2021-10-11 00:00:00  1 days 07:00:00   
3596       51944  27064.0  2021-10-11 00:00:00  1 days 08:00:00   
3597       51945  27064.0  2021-10-11 00:00:00  1 days 09:00:00   
3598       51946  27064.0  2021-10-11 00:00:00  1 days 10:00:00   
3599       51947  27064.0  2021-10-11 00:00:00  1 days 11:00:00   

              pv_datetime  pv_hour  horizon  generation  capacity  \
0     2018-11-15 16:00:00     16.0      1.0     0.00000       4.0   
1     2018-11-15 17:00:00     17.0      2.0     0.00000       4.0   
2     2018-11-15 18:00:00     18.0      3.0     0.00000       4.0   
3     2018-11-15 19:00:00     19.0      4.0     0.00000       4.0   
4     2018-11-15 20:00:00     20.0      5.0     0.00000       4.0   
...                   ...      ...      ...         ...       ...   
3595  2021-10-12 11:00:00     11.0     32.0   908.97120       2.0   
3596  2021-10-12 12:00:00     12.0     33.0  1400.04000       2.0   
3597  2021-10-12 13:00:00     13.0     34.0   254.46000       2.0   
3598  2021-10-12 14:00:00     14.0     35.0   266.73720       2.0   
3599  2021-10-12 15:00:00     15.0     36.0    46.82088       2.0   

      normalize_generation  ...       lcc       mcc  sde        sr        t2m  \
0                 0.000000  ...  0.963867  0.261536  0.0       0.0  286.73633   
1                 0.000000  ...  1.000000  0.115631  0.0  526976.0  287.06274   
2                 0.000000  ...  1.000000  0.020874  0.0  133376.0  286.91820   
3                 0.000000  ...  0.998901  0.215607  0.0   11136.0  286.92578   
4                 0.000000  ...  1.000000  0.305634  0.0   35328.0  286.54468   
...                    ...  ...       ...       ...  ...       ...        ...   
3595            454.485596  ...  0.069977  0.841431  0.0  181760.0  281.04980   
3596            700.020020  ...  0.089294  0.284546  0.0  289280.0  282.81665   
3597            127.230003  ...  0.084595  0.744873  0.0  920064.0  284.67114   
3598            133.368607  ...  0.073120  0.917603  0.0  669184.0  285.73510   
3599             23.410440  ...  0.522461  0.932526  0.0  573952.0  286.84840   

           tcc       u10      u100       v10      v100  
0     0.971954 -2.419031 -3.132269  5.898019  8.501874  
1     1.000000 -2.717444 -3.569618  5.633824  7.929080  
2     1.000000 -2.529895 -3.632496  5.222868  7.941486  
3     0.999115 -2.069286 -2.887247  4.480828  7.139501  
4     1.000000 -2.679039 -3.784738  4.528837  7.023499  
...        ...       ...       ...       ...       ...  
3595  0.946198  2.619058  4.780936 -1.124188 -3.762029  
3596  0.891418  3.065713  4.840455 -1.597640 -3.979417  
3597  0.904755  3.102398  4.357941 -2.269724 -3.671457  
3598  0.933502  3.113303  4.248115 -3.022680 -4.408169  
3599  0.967194  2.722497  3.754231 -4.518713 -6.261210  

[3600 rows x 28 columns]

In [5]:
test_data = test_data.drop(columns=['Unnamed: 0'])
test_data.columns

Index(['ss_id', 'init_time', 'step', 'pv_datetime', 'pv_hour', 'horizon',
       'generation', 'capacity', 'normalize_generation', 'lat', 'long', 'tilt',
       'orientation', 'dlwrf', 'dswrf', 'duvrs', 'hcc', 'lcc', 'mcc', 'sde',
       'sr', 't2m', 'tcc', 'u10', 'u100', 'v10', 'v100'],
      dtype='object')

In [25]:
best_model_path = '../lightning_logs/my_model/version_21/checkpoints/epoch=45-step=1380.ckpt'
best_tft = TemporalFusionTransformer.load_from_checkpoint(best_model_path)


In [7]:
best_tft = TemporalFusionTransformer.load_from_checkpoint(best_model_path)

In [9]:
max_encoder_length = 36
max_prediction_length = 36

test_data.rename(columns={'pv_hour': 'day_hour'}, inplace=True)

test_data['ss_id'] = test_data['ss_id'].astype(int)

test_data['pv_datetime'] = pd.to_datetime(test_data['pv_datetime'])
test_data['date'] = test_data['pv_datetime'].dt.date
test_data['day_of_week'] = test_data['pv_datetime'].dt.dayofweek
test_data['month'] = test_data['pv_datetime'].dt.month

test_data['ss_id'] = test_data['ss_id'].astype(str)
test_data['day_of_week'] = test_data['day_of_week'].astype(str)
test_data['month'] = test_data['month'].astype(str)
test_data['day_hour'] = test_data['day_hour'].astype(str)

test_data['time_idx'] = test_data.index
test_data['time_idx'] = test_data['time_idx'].astype(int)

In [11]:
test_data.shape

(3600, 31)

In [12]:
new_data = TimeSeriesDataSet(
    test_data,
    time_idx="time_idx",
    target="normalize_generation",
    group_ids=["ss_id"],  # Grouping by ss_id to identify different PV sites
    min_encoder_length=max_encoder_length // 2,
    max_encoder_length=max_encoder_length,
    min_prediction_length=1,
    max_prediction_length=max_prediction_length,
    static_reals=["capacity", "lat", "long", "tilt", "orientation"],
    time_varying_known_categoricals=[ "month", "day_of_week", "day_hour"],
    time_varying_known_reals=["time_idx", "dlwrf", "dswrf", "duvrs", "hcc", "lcc", "mcc", "sde", "sr", "t2m", "tcc", "u10", "u100", "v10", "v100"],
    time_varying_unknown_reals=["normalize_generation"],
    add_relative_time_idx=True,
    add_target_scales=True,
    add_encoder_length=True,
    allow_missing_timesteps=False,
)


In [13]:
new_data_loader = new_data.to_dataloader(train=False, batch_size=128, num_workers=2)

In [14]:
# lightning_logs/my_model/version_20/checkpoints/epoch=49-step=1500.ckpt
# actuals = torch.cat([y[0] for x, y in iter(val_dataloader)])
# predictions = best_tft.predict(val_dataloader)

In [15]:
actuals = torch.cat([y[0] for x, y in iter(new_data_loader)])

/Users/rosh/Desktop/gsoc/gsoc-open-quartz/.venv/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/rosh/Desktop/gsoc/gsoc-open-quartz/.venv/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/rosh/Desktop/gsoc/gsoc-open-quartz/.venv/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/rosh/Desktop/gsoc/gsoc-open-quartz/.venv/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/rosh/Desktop/gsoc/gsoc-open-quartz/.venv/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature nam

In [16]:
predictions = best_tft.predict(new_data_loader)

GPU available: True (mps), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
/Users/rosh/Desktop/gsoc/gsoc-open-quartz/.venv/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/rosh/Desktop/gsoc/gsoc-open-quartz/.venv/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/rosh/Desktop/gsoc/gsoc-open-quartz/.venv/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/rosh/Desktop/gsoc/gsoc-open-quartz/.venv/lib/python3.10/site-packages/sklearn/base.py:493: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/Users/rosh/Desktop/gsoc/gsoc

In [17]:
print("Checking for NaN values in actuals and predictions...")
print("Number of NaNs in actuals:", torch.isnan(actuals).sum().item())
print("Number of NaNs in predictions:", torch.isnan(predictions).sum().item())

Checking for NaN values in actuals and predictions...
Number of NaNs in actuals: 0
Number of NaNs in predictions: 35208


In [19]:

# mae = (actuals - predictions).abs().mean().item()
# print(f"Mean Absolute Error: {mae}")


# average_p50_loss = (actuals - predictions).abs().mean(axis=1)
# print(f"Average P50 Loss per Time Series: {average_p50_loss}")


In [20]:
print("Actuals:", actuals.tolist())
print("Predictions:", predictions.tolist())

Actuals: [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 146.5113067626953, 251.7209930419922, 300.4230041503906, 317.4930114746094, 397.4580078125, 395.8500061035156, 353.5799865722656, 263.70361328125, 185.38619995117188, 98.48880004882812, 2.6986650482285768e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 146.5113067626953, 251.7209930419922, 300.4230041503906, 317.4930114746094, 397.4580078125, 395.8500061035156, 353.5799865722656, 263.70361328125, 185.38619995117188, 98.48880004882812, 2.6986650482285768e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 146.5113067626953, 251.7209930419922, 300.4230041503906, 317.4930114746094, 397.4580078125, 395.8500061035156, 353.5799865722656, 263.70361328125, 185.38619995117188, 98.48880004882812, 2.6986650482285768e-05, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 

In [21]:
print(actuals)

tensor([[  0.0000,   0.0000,   0.0000,  ...,   0.0000,   0.0000,   0.0000],
        [  0.0000,   0.0000,   0.0000,  ...,   0.0000,   0.0000,   0.0000],
        [  0.0000,   0.0000,   0.0000,  ...,   0.0000,   0.0000,   0.0000],
        ...,
        [  0.0000,   0.0000,   0.0000,  ..., 274.7082, 454.4856, 700.0200],
        [  0.0000,   0.0000,   0.0000,  ..., 454.4856, 700.0200, 127.2300],
        [  0.0000,   0.0000,   0.0000,  ..., 700.0200, 127.2300, 133.3686]])


In [23]:
# mask = ~torch.isnan(actuals) & ~torch.isnan(predictions)
# actuals_filtered = actuals[mask]
# predictions_filtered = predictions[mask]

# # Calculate MAE
# mae = (actuals_filtered - predictions_filtered).abs().mean().item()
# print(f"Mean Absolute Error: {mae}")


In [28]:
print("Shape of actuals:", actuals.shape)
print("Shape of predictions:", predictions.shape)


Shape of actuals: torch.Size([35, 18])
Shape of predictions: torch.Size([35, 18])


In [29]:
print(f"Actuals size: {actuals.size()}")
print(f"Predictions size: {predictions.size()}")

Actuals size: torch.Size([35, 18])
Predictions size: torch.Size([35, 18])
